### Load libraries and external data

In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import colored
from colored import stylize
from data import dataloader
import json
from neuralnet import nn
import numpy as np
import pandas as pd
import pixiedust_node #v≥0.2.5

Pixiedust database opened successfully


#### Load data from Firebase.
Requires [Firebase service account credentials](https://console.firebase.google.com/project/tingle-pilot-collected-data/settings/serviceaccounts/adminsdk) in JSON format saved in `./firebase-credentials`.

In [3]:
pilot_data, notes = dataloader.load_from_firebase(notes=True)
pilot_data = dataloader.break_out_blocks(pilot_data)

pixiedust_node 0.2.5 started. Cells starting '%%node' may contain Node.js code.
Data loaded from Firebase!


#### Load [Synaptic](http://caza.la/synaptic/)
If "Error: Cannot find module 'synaptic'", create and run these two cells:

1. ```
cd neuralnet
```

2. ```sh
!npm init -y
!npm install -s synaptic
```

In [5]:
%%node
var lstm = require('../../tingle-pilot-study/neuralnet/lstm.js');

---
### See all targets, number of available samples and iteration blocks

In [6]:
for target in list(pilot_data.target.unique()):
    ib =max(
        pilot_data.loc[
            pilot_data.target==target
        ].iteration_block.dropna()
    )
    print(": ".join([
        target,
        "{0} on-target samples in {1} iteration block{2}".format(
            str(len(pilot_data.loc[
                (pilot_data.target == target) &
                (pilot_data.ontarget)
            ])),
            "%.0f" % ib,
            "s" if ib != 1 else ""
        )
    ]))

none: 19 on-target samples in 2 iteration blocks
environment: 106 on-target samples in 4 iteration blocks
body: 101 on-target samples in 2 iteration blocks
cup: 33 on-target samples in 3 iteration blocks
food: 35 on-target samples in 4 iteration blocks
nails: 69 on-target samples in 3 iteration blocks
smoke: 92 on-target samples in 3 iteration blocks
eyebrow: 235 on-target samples in 5 iteration blocks
nose: 249 on-target samples in 4 iteration blocks
above-ear: 403 on-target samples in 5 iteration blocks
behind-ear: 220 on-target samples in 4 iteration blocks
opposite-cheek: 74 on-target samples in 6 iteration blocks
chin: 166 on-target samples in 1 iteration block
cheek: 686 on-target samples in 6 iteration blocks
forehead: 176 on-target samples in 1 iteration block
top-head: 160 on-target samples in 1 iteration block
back-head: 170 on-target samples in 1 iteration block
opposite-face: 381 on-target samples in 2 iteration blocks
paint-mouth: 81 on-target samples in 3 iteration blocks

---
### Extract training and testing data
Define targets of interest and corresponding offtargets

In [7]:
with open(
    'data/targets.json',
    'r'
) as fp:
    targets = json.load(
        fp
    )[0]

Set parameters for nn:

In [8]:
input_signals = [
    "distance",
    "thermopile1",
    "thermopile2",
    "thermopile3",
    "thermopile4"
]
iteration_blocks = list(range(1,7))
n_samples = 100

Get training inputs and outputs, inputs that should evaluate ~true and inputs that should evaluate ~false

In [9]:
data = {}
for target in targets:
    data[target] = {
        "train": nn.define_trainer_data(
            pilot_data,
            {
                "target": [target],
                "offtarget": targets[target]
            },
            input_signals,
            iteration_blocks,
            n_samples
        ),
        "test_true": nn.define_activation(
            pilot_data,
            [target],
            input_signals,
            iteration_blocks,
            exclude=n_samples
        ),
        "test_false": nn.define_activation(
            pilot_data,
            targets[target],
            input_signals,
            iteration_blocks,
            exclude=n_samples
        )
    }

Preview all inputs and training outputs

In [10]:
data

{'above-ear': {'test_false': [[0.0,
    0.8183760683760684,
    0.8719646799116998,
    0.8660812294182219,
    0.8551042810098793],
   [0.0,
    0.8162393162393163,
    0.8719646799116998,
    0.8507135016465424,
    0.8375411635565313],
   [0.0,
    0.811965811965812,
    0.870860927152318,
    0.8342480790340286,
    0.8342480790340286],
   [0.0,
    0.811965811965812,
    0.858719646799117,
    0.8441273326015369,
    0.8441273326015369],
   [0.0,
    0.8205128205128205,
    0.8664459161147904,
    0.8562019758507136,
    0.8616904500548848],
   [0.0,
    0.8322649572649574,
    0.8730684326710817,
    0.8496158068057081,
    0.8616904500548848],
   [0.6095617529880478,
    0.8376068376068377,
    0.9061810154525386,
    0.8957189901207464,
    0.8902305159165752],
   [0.0,
    0.8429487179487181,
    0.9061810154525386,
    0.9088913282107575,
    0.8792535675082327],
   [0.09163346613545817,
    0.8429487179487181,
    0.9094922737306844,
    0.9055982436882547,
    0.87925356750

**Note**: These data take some time to copy across environments. Give the notebook some time between running cells across Python and JavaScript.

---
### Train and test

In [52]:
%%node
var networks = {};
for (var target in data) {
  networks[target] = lstm.train_lstm([5,5,2,1], data[target]["train"], 0.06, 0.06, 3000);
}

iterations 2510 error 0.0757908940981634 rate 0.06
iterations 2515 error 0.0770497113928965 rate 0.06
iterations 2520 error 0.07549272401704003 rate 0.06
iterations 2525 error 0.07704775955749288 rate 0.06
iterations 2530 error 0.07657882155491216 rate 0.06
iterations 2535 error 0.0768632829563464 rate 0.06
iterations 2540 error 0.07593946070965435 rate 0.06
iterations 2545 error 0.07632940663148127 rate 0.06
iterations 2550 error 0.07713653924637583 rate 0.06
iterations 2555 error 0.07674219471430602 rate 0.06
iterations 2560 error 0.07490273324333069 rate 0.06
iterations 2565 error 0.07510481598422361 rate 0.06
iterations 2570 error 0.0748818767166537 rate 0.06
iterations 2575 error 0.07730769229674711 rate 0.06
iterations 2580 error 0.07629596653285302 rate 0.06
iterations 2585 error 0.07571269723697219 rate 0.06
iterations 2590 error 0.07641465239999436 rate 0.06
iterations 2595 error 0.07627415711364989 rate 0.06
iterations 2600 error 0.07540969451470088 rate 0.06
iterations 2605 

In [56]:
%%node
var test_outputs = {};
for (var target in data) {
    test_outputs[target] = {"true":[],"false":[]};
    for(var iteration=0; iteration < data[target]["test_true"].length; iteration++){
      test_outputs[target]["true"].push(networks[target].activate(data[target]["test_true"][iteration]));
      }
    for(var iteration=0; iteration < data[target]["test_false"].length; iteration++){
      test_outputs[target]["false"].push(networks[target].activate(data[target]["test_false"][iteration]));
    }
}

... ... ..... ..... ... ..... ..... ...


In [57]:
test_outputs

{'above-ear': {'false': [[0.0024033584737394144],
   [0.0005384299707692199],
   [7.173028112816379e-05],
   [0.0003725084545192804],
   [0.001242225370643566],
   [0.0012697065916093219],
   [1.9879385229189213e-06],
   [0.19138809649932564],
   [0.02914974018219421],
   [0.31092425012549574],
   [0.1493106083191187],
   [0.14077230148107928],
   [0.00906211152371387],
   [0.4100302905391476],
   [0.25642923390181616],
   [0.18877925553538885],
   [0.07112828051021344],
   [0.2767035241917502],
   [0.29168431499020236],
   [0.10466213538909327],
   [0.04107546067100517],
   [0.3333060518523398],
   [0.14133147286293532],
   [0.17144818891884878],
   [0.06509878094477399],
   [0.08195194178165138],
   [0.08682463844057997],
   [0.17881110171600847],
   [0.13042061344889927],
   [0.11124819979964291],
   [0.1426392739760865],
   [0.01460051397376065],
   [0.34327512095798746],
   [0.13564982439766082],
   [0.1043191013235002],
   [0.06531329916337764],
   [0.15819130658227762],
   [0.22

---
### See outputs

If the training is adequate x ≈ 0 ∀ x in the following:

In [58]:
f = {target: [
        outputs for outputs in test_outputs[target]['false']
] for target in targets}
f

{'above-ear': [[0.0024033584737394144],
  [0.0005384299707692199],
  [7.173028112816379e-05],
  [0.0003725084545192804],
  [0.001242225370643566],
  [0.0012697065916093219],
  [1.9879385229189213e-06],
  [0.19138809649932564],
  [0.02914974018219421],
  [0.31092425012549574],
  [0.1493106083191187],
  [0.14077230148107928],
  [0.00906211152371387],
  [0.4100302905391476],
  [0.25642923390181616],
  [0.18877925553538885],
  [0.07112828051021344],
  [0.2767035241917502],
  [0.29168431499020236],
  [0.10466213538909327],
  [0.04107546067100517],
  [0.3333060518523398],
  [0.14133147286293532],
  [0.17144818891884878],
  [0.06509878094477399],
  [0.08195194178165138],
  [0.08682463844057997],
  [0.17881110171600847],
  [0.13042061344889927],
  [0.11124819979964291],
  [0.1426392739760865],
  [0.01460051397376065],
  [0.34327512095798746],
  [0.13564982439766082],
  [0.1043191013235002],
  [0.06531329916337764],
  [0.15819130658227762],
  [0.22877241309257174],
  [0.08630250655459577],
  [0

If the training is adequate x ≈ 1 ∀ x in the following:

In [59]:
t = {target: [
        outputs for outputs in test_outputs[target]['true']
] for target in targets}
t

{'above-ear': [[0.2951166349552578],
  [0.08517565388108295],
  [0.09339365387818993],
  [0.2767809973322742],
  [0.1655378306660714],
  [0.0617097807086395],
  [0.05264832280316263],
  [0.13928256467820618],
  [0.18351670122597324],
  [0.1700602198701363],
  [0.5415400477845174],
  [0.4134321672904289],
  [0.22711235952562953],
  [0.07326598028896471],
  [0.17695939446712933],
  [0.31352075519289857],
  [0.39838007459290936],
  [0.3332610791190562],
  [0.16112188476460976],
  [0.40523327107162926],
  [0.34072378662088615],
  [0.23020406383260802],
  [0.04471152786173932],
  [0.40885149281690786],
  [0.3506151298886552],
  [0.38787130371659484],
  [0.11394150914274083],
  [0.3862348437585612],
  [0.32757939140597325],
  [0.2157764043192805],
  [0.06629042911472947],
  [0.0022650974268908796],
  [0.007818917590535945],
  [0.03171276832904347],
  [0.11118812740273284],
  [0.1825949106888853],
  [0.04519640695758065],
  [0.2774306160867671],
  [0.17250188799191232],
  [0.22710142535605216

Finally, if training is adequate, f ≪ t:

In [62]:
f_mean = {
    target: np.mean(f[target]) for target in targets if target in f and len(f[target])
}
t_mean = {
    target: np.mean(t[target]) for target in targets if target in t and len(t[target])
}
for target in t_mean:
    print(target)
    print(
        "f = {0}\nt = {1}\n{0} ≪ {1} ?\n".format(
            str(f_mean[target]),
            str(t_mean[target])
        ) if f_mean[target] < t_mean[target] else "f = {0}\nt = {1}\n{2}".format(
            str(f_mean[target]),
            str(t_mean[target]),
            stylize(
                "Nope. f > t\n",
                colored.fg("red")
            )
        )
    )
for target in t_mean:
    print("{0}: f = {1:.4f} < t = {2:.4f}".format(
        target,
        f_mean[target],
        t_mean[target]
    ))

eyebrow
f = 0.006145158587230735
t = 0.03577201297345927
0.006145158587230735 ≪ 0.03577201297345927 ?

nose
f = 0.006040420779263561
t = 0.0026361894328427687
Nope. f > t

above-ear
f = 0.034208733624127186
t = 0.23525974186821738
0.034208733624127186 ≪ 0.23525974186821738 ?

behind-ear
f = 0.032417511634781515
t = 0.10890339441424839
0.032417511634781515 ≪ 0.10890339441424839 ?

chin
f = 0.018577301618111084
t = 0.1175642507189909
0.018577301618111084 ≪ 0.1175642507189909 ?

cheek
f = 0.017876708611711947
t = 0.050971347837739205
0.017876708611711947 ≪ 0.050971347837739205 ?

forehead
f = 0.02094239224694073
t = 0.1447758401246034
0.02094239224694073 ≪ 0.1447758401246034 ?

top-head
f = 0.009497771932739579
t = 0.4202928106232783
0.009497771932739579 ≪ 0.4202928106232783 ?

back-head
f = 0.020932451022349006
t = 0.21096976337249457
0.020932451022349006 ≪ 0.21096976337249457 ?

opposite-face
f = 0.004765466556028696
t = 0.15770510358821796
0.004765466556028696 ≪ 0.15770510358821796 ?



---
### Try with demo data

In [43]:
with open(
    'data/demo_data.json',
    'r'
) as fp:
    demo_data = json.load(
        fp
    )[0]

In [44]:
scale = list(
    pd.DataFrame(
        [
            a[0:5] for a in [
                *demo_data["true"],
                *demo_data["false"]
            ]
        ]
    ).astype('float').max(axis=0)
)
demo_test = {
    "train":[
        *[{
            "input": [
                float(d)/scale[datum_i] for datum_i, d in enumerate(datum[0:5])
            ],
            "output": [1]
        } for datum in demo_data["true"][0:40]],
        *[{
            "input": [
                float(d)/scale[datum_i] for datum_i, d in enumerate(datum[0:5])
            ],
            "output": [0]
        } for datum in demo_data["false"][0:40]]
    ],
    "test_true": [[
                float(d)/scale[datum_i] for datum_i, d in enumerate(datum[0:5])
            ] for datum in demo_data["true"][41:]],
    "test_false": [[
                float(d)/scale[datum_i] for datum_i, d in enumerate(datum[0:5])
            ] for datum in demo_data["false"][41:]]
}

In [45]:
%%node
var LSTM5 = lstm.train_lstm([5,5,2,1], demo_test["train"], 0.06, 0.06, 3000);

TRAINING 🏋 interations:3000 🏋 minimum error:0.06 🏋 rate:0.06
iterations 5 error 0.7176128541888434 rate 0.06
iterations 10 error 0.6982012337977093 rate 0.06
iterations 15 error 0.6995249375563095 rate 0.06
iterations 20 error 0.7141898165156951 rate 0.06
iterations 25 error 0.6960532606961647 rate 0.06
iterations 30 error 0.6963383983849549 rate 0.06
iterations 35 error 0.6850008782401906 rate 0.06
iterations 40 error 0.6869078844078922 rate 0.06
iterations 45 error 0.6762224066302895 rate 0.06
iterations 50 error 0.683080201668908 rate 0.06
iterations 55 error 0.6750890815014035 rate 0.06
iterations 60 error 0.6514714847116037 rate 0.06
iterations 65 error 0.6524198896480392 rate 0.06
iterations 70 error 0.6609594394153746 rate 0.06
iterations 75 error 0.6463336047473002 rate 0.06
iterations 80 error 0.6430200121025785 rate 0.06
iterations 85 error 0.6519285556573546 rate 0.06
iterations 90 error 0.643228766862508 rate 0.06
iterations 95 error 0.6343045939692862 rate 0.06
iterations 

In [47]:
%%node
var demo_test_outputs = {"true":[],"false":[]}
for(var iteration=0; iteration < demo_test["test_true"].length; iteration++){
    var op = LSTM5.activate(demo_test["test_true"][iteration]);
    demo_test_outputs["true"].push(op);
}
for(var iteration=0; iteration < demo_test["test_false"].length; iteration++){
    demo_test_outputs["false"].push(LSTM5.activate(demo_test["test_false"][iteration]));
}

... ... ...
... ...


In [48]:
demo_test_outputs

{'false': [[0.9369284419405952],
  [0.9718886796832733],
  [0.8604860261178248],
  [0.5561251992379272],
  [0.016624282208243704],
  [0.00039240757018500636],
  [2.0184519711395964e-05],
  [9.717991816267999e-06],
  [3.2620037903688403e-06]],
 'true': [[0.9250166953343892],
  [0.9274044493231222],
  [0.996783304361895],
  [0.9968793152438503],
  [0.9969938749551247],
  [0.9821942859921602],
  [0.9863869855548448],
  [0.9757638908681954],
  [0.996742625262968]]}

In [49]:
np.mean(demo_test_outputs['false'])

0.3713864668081519

In [50]:
np.mean(demo_test_outputs['true'])

0.9760183807662833